<a href="https://colab.research.google.com/github/faithNassiwa/predictive-diagnosis-assistant/blob/main/notebooks/Refinement_DDXPlus_GradientBoosting.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [101]:
# Import required libraries
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
warnings.filterwarnings('ignore')
from sklearn import preprocessing
from sklearn.metrics import accuracy_score, classification_report, auc, roc_auc_score, roc_curve, confusion_matrix
from pprint import pprint
from xgboost import XGBClassifier, plot_importance, DMatrix
from sklearn.utils import class_weight
from sklearn.model_selection import GridSearchCV, KFold, ParameterGrid
from sklearn.preprocessing import LabelBinarizer

In [ ]:
# Mount google drive to access folder with data
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


# Data Load and Preprocessing

In [ ]:
# Read the training and test dataset -- Took a minute

train_df = pd.read_csv('/content/drive/MyDrive/DS5500/Data/Dataset2/processed_train.csv', low_memory=False)
test_df = pd.read_csv('/content/drive/MyDrive/DS5500/Data/Dataset2/processed_test.csv', low_memory=False)
pprint(f'Train dataset shape: {train_df.shape}')
pprint(f'Test dataset shape: {test_df.shape}')

'Train dataset shape: (1025602, 221)'
'Test dataset shape: (134529, 221)'


In [ ]:
# View values of categorical columns
unique_values = {col: train_df[col].unique() for col in train_df.columns if train_df[col].dtype == 'O'}
pprint(unique_values)


{'Characterize your pain:': array(['heavy', 'exhausting', 'sharp', 'burning', 'a cramp', '0',
       'heartbreaking', 'sickening', 'sensitive', 'scary',
       'a knife stroke', 'tugging', 'violent', 'a pulse', 'haunting',
       'tedious', nan], dtype=object),
 'Do you feel pain somewhere?': array(['temple(L)', 'posterior chest wall(L)', 'eye(R)', 'pharynx', '0',
       'temple(R)', 'epigastric', 'breast(L)', 'iliac fossa(L)', 'pubis',
       'occiput', 'testicle(L)', 'posterior chest wall(R)', 'shoulder(L)',
       'under the jaw', 'hypochondrium(R)', 'forehead', 'trachea',
       'sole(L)', 'finger (middle)(R)', 'shoulder(R)', 'breast(R)',
       'dorsal aspect of the foot(L)', 'belly', 'eye(L)', 'nose',
       'hip(L)', 'top of the head', 'triceps(R)', 'finger (middle)(L)',
       'ear(L)', 'ear(R)', 'nowhere', 'sole(R)', 'upper chest',
       'cheek(L)', 'hypochondrium(L)', 'knee(R)', 'back of head',
       'palace', 'testicle(R)', 'lower chest',
       'dorsal aspect of the foot(

In [ ]:
# Check if there are any nans values
pprint(train_df.columns[train_df.isna().any()].tolist())
pprint(test_df.columns[test_df.isna().any()].tolist())

['Characterize your pain:', 'What color is the rash?']
['Characterize your pain:', 'What color is the rash?']


In [ ]:
# Count of NAN in the columns -- drop these rows

print(train_df['Characterize your pain:'].isna().sum())
print(train_df['What color is the rash?'].isna().sum())
print(test_df['Characterize your pain:'].isna().sum())
print(test_df['What color is the rash?'].isna().sum())

10859
32609
1379
4436


In [ ]:
# Drop rows with NAN values

train_df_nonan = train_df.dropna(subset=['Characterize your pain:', 'What color is the rash?'])
test_df_nonan = test_df.dropna(subset=['Characterize your pain:', 'What color is the rash?'])

In [ ]:
# Count of NAN in the columns after drop

print(train_df_nonan['Characterize your pain:'].isna().sum())
print(train_df_nonan['What color is the rash?'].isna().sum())
print(test_df_nonan['Characterize your pain:'].isna().sum())
print(test_df_nonan['What color is the rash?'].isna().sum())

0
0
0
0


In [ ]:
pprint(f'Train dataset shape: {train_df_nonan.shape}')
pprint(f'Test dataset shape: {test_df_nonan.shape}')

'Train dataset shape: (982224, 221)'
'Test dataset shape: (128726, 221)'


In [ ]:
# Remove columns with only one value
train_df_nonan.drop(columns=['Have you lost consciousness associated with violent and sustained muscle contractions or had an absence episode?',
                             'Have you noticed a diffuse (widespread) redness in one or both eyes?',
                             'Have you had any vaginal discharge?'], inplace=True)
test_df_nonan.drop(columns=['Have you lost consciousness associated with violent and sustained muscle contractions or had an absence episode?',
                             'Have you noticed a diffuse (widespread) redness in one or both eyes?',
                             'Have you had any vaginal discharge?'], inplace=True)

In [ ]:
pprint(f'Train dataset shape: {train_df_nonan.shape}')
pprint(f'Test dataset shape: {test_df_nonan.shape}')

'Train dataset shape: (982224, 218)'
'Test dataset shape: (128726, 218)'


# Feature Engineering

In [ ]:
# Handling Categorical Variables  - Label Encoding to avoid creating new features that increase the already many featureset
from sklearn.preprocessing import LabelEncoder

categorical_columns = list(unique_values.keys())

# Reset indices of both X_train and X_test
train_df_reset = train_df_nonan.reset_index(drop=True)
test_df_reset = test_df_nonan.reset_index(drop=True)

# Combine the train and test data
combined = pd.concat([train_df_reset, test_df_reset], axis=0)

# Create a dictionary to store encodings
label_encoders = {}


# Label encode the combined dataframe for each categorical column
for col in categorical_columns:
  le = LabelEncoder()
  combined[col] = le.fit_transform(combined[col])
  label_encoders[col] = le

combined_encoded = combined

# Split the combined_encoded dataframe back into train and test
train_encoded = combined_encoded.iloc[:len(train_df_nonan)]
test_encoded = combined_encoded.iloc[len(train_df_nonan):]

In [ ]:
# Prepare training and test variables
X_columns = [col for col in train_df_nonan.columns if col not in ['Unnamed: 0', 'PATHOLOGY']]
X_train = train_encoded[X_columns]
y_train = train_encoded['PATHOLOGY']
X_test = test_encoded[X_columns]
y_test = test_encoded['PATHOLOGY']
pprint(f'X_train shape: {X_train.shape}')
pprint(f'y_train shape: {y_train.shape}')
pprint(f'X_test shape: {X_test.shape}')
pprint(f'y_test shape: {y_test.shape}')


'X_train shape: (982224, 216)'
'y_train shape: (982224,)'
'X_test shape: (128726, 216)'
'y_test shape: (128726,)'


In [ ]:
# Check dimension after encoding
pprint(f'X_train shape: {X_train.shape}')
pprint(f'X_test shape: {X_test.shape}')

'X_train shape: (982224, 216)'
'X_test shape: (128726, 216)'


# Feature Selection

In [ ]:
# Correlation Analysis
correlation_matrix = X_train.corr()
correlation_matrix.style.background_gradient(cmap='cool')

In [ ]:
## Export correlation matrix
correlation_matrix.to_csv('/content/drive/MyDrive/DS5500/Data/Dataset2/correlation_matrix.csv')

In [51]:
# Get pair where value is greater 0.6 coefficient, highly and positive correlation
correlated_features = set()
for i in range(len(correlation_matrix.columns)):
    for j in range(i):
        if abs(correlation_matrix.iloc[i, j]) > 0.6:
            print(f'Feature: {correlation_matrix.columns[i]} and {correlation_matrix.columns[j]} have correlation of {abs(correlation_matrix.iloc[i, j])}')
            correlated_features.add(correlation_matrix.columns[i])
            correlated_features.add(correlation_matrix.columns[j])

Feature: Characterize your pain: and Do you have pain somewhere, related to your reason for consulting? have correlation of 0.7012969715899394
Feature: Do you feel pain somewhere? and Do you have pain somewhere, related to your reason for consulting? have correlation of 0.6710697244517296
Feature: Does the pain radiate to another location? and Do you have pain somewhere, related to your reason for consulting? have correlation of 0.8592614941708604
Feature: Does the pain radiate to another location? and Characterize your pain: have correlation of 0.6404300039414924
Feature: Have you ever had a sexually transmitted infection? and Do you have swollen or painful lymph nodes? have correlation of 0.6555725336207763
Feature: Have you had unprotected sex with more than one partner in the last 6 months? and Do you have swollen or painful lymph nodes? have correlation of 0.6545784189561947
Feature: Have you had unprotected sex with more than one partner in the last 6 months? and Have you ever ha

In [52]:
print(f'Number of correlated features: {len(correlated_features)}')
pprint(f'Correlated features: {correlated_features}')

Number of correlated features: 125
("Correlated features: {'Have any of your family members ever had a "
 "pneumothorax?', 'Have you ever had surgery to remove lymph nodes?', 'Have "
 'you ever had a migraine or is a member of your family known to have '
 "migraines?', 'Do you have swelling in one or more areas of your body?', 'Do "
 "you work in construction?', 'Do you have trouble keeping your tongue in your "
 "mouth?', 'Do you suffer from chronic anxiety?', 'Do you have any family "
 "members who have been diagnosed with anemia?', 'Have you started or taken "
 "any antipsychotic medication within the last 7 days?', 'Are there any "
 "members of your family who have been diagnosed myasthenia gravis?', 'Do any "
 "members of your immediate family have a psychiatric illness?', 'Have you "
 "been in contact with a person with similar symptoms in the past 2 weeks?', "
 "'Do you have an active cancer?', 'In the last month, have you been in "
 "contact with anyone infected with the Ebola 

In [ ]:
# Get pair where value is less than -0.6 coefficient, highly and negative correlation
for i in range(len(correlation_matrix.columns)):
    for j in range(i):
        if abs(correlation_matrix.iloc[i, j]) < -0.6:
            print(f'Feature: {correlation_matrix.columns[i]} and {correlation_matrix.columns[j]} have correlation of {abs(correlation_matrix.iloc[i, j])}')

Correlation Matrix Findings: Using a threashold of +0.5 and -0.5


1.   Age is not highly correlated to any other feature
2.   Sex is not highly correlated to any other feature
3. 'Do you live with 4 or more people?' is highly positive correlated to 'Do you attend or work in a daycare?' and 'Have you been in contact with a person with similar symptoms in the past 2 weeks?'
4. 'Do you have pain somewhere, related to your reason for consulting?' is highly positively correlated to 'Characterize your pain:', 'Do you feel pain somewhere?', 'Does the pain radiate to another location?'
5. 'Characterize your pain:' is highly positive correlated to 'Do you have pain somewhere, related to your reason for consulting?', 'Does the pain radiate to another location?'
6. 'Do you feel pain somewhere?' is highly positive correlated to 'Do you feel pain somewhere?'
7. 'Does the pain radiate to another location?' is highly postive correlated to ' Do you have pain somewhere, related to your reason for consulting?', 'Characterize your pain:'
8. 'Do you have a cough that produces colored or more abundant sputum than usual?' is highly positive correlated to 'Do you have a chronic obstructive pulmonary disease (COPD)?'
9. 'Do you smoke cigarettes?' is not highly correlated to any other feature
10. 'Do you have a fever (either felt or measured with a thermometer)?' is not highly correlated to any other feature
11. 'Do you have a sore throat?' is not highly correlated to any other feature
12. 'Do you have a cough?' is not highly correlated to any other feature
13. 'Have you traveled out of the country in the last 4 weeks?' is not highly correlated to any other feature

14. 'Are you exposed to secondhand cigarette smoke on a daily basis?' is not highly  correlated to any other feature

15. 'Do you have swollen or painful lymph nodes?' is highly positive correlated to 'Have you ever had a sexually transmitted infection?', 'Have you had unprotected sex with more than one partner in the last 6 months?', ' Have you had sexual intercourse with an HIV-positive partner in the past 12 months?'

16. 'Have you ever had a sexually transmitted infection?' is highly positive correlated to 'Do you have swollen or painful lymph nodes?',' Have you had unprotected sex with more than one partner in the last 6 months?' , ' Have you had sexual intercourse with an HIV-positive partner in the past 12 months?' , ' Are you currently using intravenous drugs?'

17. 'Have you had diarrhea or an increase in stool frequency?' is highly correlated to ' Is the lesion (or are the lesions) larger than 1cm?'

18. 'Have you had unprotected sex with more than one partner in the last 6 months?' is highly positive correlated to 'Do you have swollen or painful lymph nodes?', 'Have you ever had a sexually transmitted infection?', 'Have you had sexual intercourse with an HIV-positive partner in the past 12 months?', 'Are you currently using intravenous drugs?'

19. 'Do you have any lesions, redness or problems on your skin that you believe are related to the condition you are consulting for?' is highly positive correlated(>0.7) to 'What color is the rash?', 'Do your lesions peel off?', 'Where is the affected region located?', 'Is the lesion (or are the lesions) larger than 1cm?'. All each related to each other

20. 'Do your lesions peel off?' highly correlated to 'Do you have any lesions, redness or problems on your skin that you believe are related to the condition you are consulting for?', 'What color is the rash?', 'Where is the affected region located?', 'Is the lesion (or are the lesions) larger than 1cm?', 'Have you had chills or shivers?', 'Do you have Parkinson’s disease?'

21. 'Where is the affected region located?' highly correlated to 'Do you have any lesions, redness or problems on your skin that you believe are related to the condition you are consulting for?', 'What color is the rash?', 'Do your lesions peel off?', 'Is the lesion (or are the lesions) larger than 1cm?'

22. 'Is the lesion (or are the lesions) larger than 1cm?' highly correlated to 'Have you had diarrhea or an increase in stool frequency?','Do you have any lesions, redness or problems on your skin that you believe are related to the condition you are consulting for?', 'What color is the rash?', 'Do your lesions peel off?', 'Where is the affected region located?'

23. 'Are you feeling nauseous or do you feel like vomiting?' not highly correlated to anything

24. 'Have you had an involuntary weight loss over the last 3 months?' not highly correlated to anything

25. 'Have you had sexual intercourse with an HIV-positive partner in the past 12 months?' is highly correlated to 'Do you have swollen or painful lymph nodes?', 'Have you ever had a sexually transmitted infection?', 'Have you had unprotected sex with more than one partner in the last 6 months?', 'Are you currently using intravenous drugs?'

26. 'Do you drink alcohol excessively or do you have an addiction to alcohol?' not highly correlated to anything

27. 'Have you had chills or shivers?' highly correlated to 'Do your lesions peel off?'

28. 'Do you have heart failure?' is highly correlated to 'Where is the swelling located?'

29. 'Have you ever had pneumonia?' is highly correlated to 'Do you have polyps in your nose?'

30. 'Do you have a chronic obstructive pulmonary disease (COPD)?' is highly correlated to 'Do you have a cough that produces colored or more abundant sputum than usual?'

31. 'Do you have asthma or have you ever had to use a bronchodilator in the past?' not highly correlated to anything

32. 'Do you have diffuse (widespread) muscle pain?' not highly correlated to anything

33. 'Have you noticed any new fatigue, generalized and vague discomfort, diffuse (widespread) muscle aches or a change in your general well-being related to your consultation today?' not highly correlated to anything

34. 'Do you have nasal congestion or a clear runny nose?' not highly correlated to anything

35. 'Do you attend or work in a daycare?' highly correlated to 'Do you live with 4 or more people?', 'Have you been in contact with a person with similar symptoms in the past 2 weeks?'

36. 'Have you lost your sense of smell?' is highly correlated to 'Do you have polyps in your nose?', 'Do you have a deviated nasal septum?', 'Have you ever been diagnosed with gastroesophageal reflux?', 'Do you have greenish or yellowish nasal discharge?'

37.


Based on the above analysis:
1. Drop - 'Do you have pain somewhere, related to your reason for consulting?' since 'Characterize your pain:', 'Do you feel pain somewhere?' and 'Does the pain radiate to another location?' can determine it
2. Drop  - 'Do you have any lesions, redness or problems on your skin that you believe are related to the condition you are consulting for?' since can be inferred 'What color is the rash?', 'Do your lesions peel off?', 'Where is the affected region located?', 'Is the lesion (or are the lesions) larger than 1cm?'.
3. Drop





In [ ]:
## get pair wise correlation of features to the target
corr_anaylsis = X_train.corrwith(y_train).sort_values()

## Display features and colleration
for index, value in corr_anaylsis.items():
  print(f'{index}: {value}')

Are you more likely to develop common allergies than the general population?: -0.28678732683703007
Are you taking any new oral anticoagulants ((NOACs)?: -0.22225973954720876
Have you noticed a wheezing sound when you exhale?: -0.21976651227655272
Have you had a cold in the last 2 weeks?: -0.21943877355592986
Have you ever had a diagnosis of anemia?: -0.21912708990858296
Do you have severe Chronic Obstructive Pulmonary Disease (COPD)?: -0.21551084863111197
Do you have chronic kidney failure?: -0.21533642610971634
Do you have a poor diet?: -0.215027406773647
Have you started or taken any antipsychotic medication within the last 7 days?: -0.2141174512461069
Have you been treated in hospital recently for nausea, agitation, intoxication or aggressive behavior and received medication via an intravenous or intramuscular route?: -0.21380861573272705
Have you ever been diagnosed with gastroesophageal reflux?: -0.21350509839516996
Do you have any family members who have been diagnosed with anemi

In [ ]:
# Export features correlation to target
corr_anaylsis.to_csv('/content/drive/MyDrive/DS5500/correlation_features_to_pathology.csv')

In [ ]:
# Perform Cross Validation  - Took 37 Minutes

from sklearn.model_selection import cross_validate

# Initialize the model
clf = XGBClassifier(random_state=0, class_weight='balanced', aplha=1.0) # include L1 regulations to prevent overfiting

# Perform cross validation
cv_results = cross_validate(clf, X_train, y_train, cv=5, scoring=['accuracy', 'precision_macro', 'recall_macro', 'f1_macro', 'roc_auc_ovr', 'roc_auc_ovo'], return_estimator=True)

# Print the mean scores
print(f'Mean Accuracy: {cv_results["test_accuracy"].mean() * 100:.2f}%')
print(f'Mean ROC_AUC OVR: {cv_results["test_roc_auc_ovr"].mean() * 100:.2f}%')
print(f'Mean ROC_AUC OVO: {cv_results["test_roc_auc_ovo"].mean() * 100:.2f}%')
print(f'Mean Precision: {cv_results["test_precision_macro"].mean() * 100:.2f}%')
print(f'Mean Recall: {cv_results["test_recall_macro"].mean() * 100:.2f}%')
print(f'Mean F1 Score: {cv_results["test_f1_macro"].mean() * 100:.2f}%')

Mean Accuracy: 99.49%
Mean ROC_AUC OVR: 99.99%
Mean ROC_AUC OVO: 99.99%
Mean Precision: 99.54%
Mean Recall: 99.30%
Mean F1 Score: 99.36%


In [ ]:
# Generate feature importances

for idx, model in enumerate(cv_results['estimator']):
    # Extract feature importances
    importances = model.feature_importances_

    # Get the feature names
    print(f'Model {idx}')
    feature_names = X_train.columns

    # Create a DataFrame for the importances
    feature_importance = pd.DataFrame({
        'Feature': feature_names,
        'Importance': importances
    })

# Sort the DataFrame by the importances
feature_importance = feature_importance.sort_values(by='Importance', ascending=False)

# Display the top features
print(feature_importance.head(50))



Model 0
Model 1
Model 2
Model 3
Model 4
                                               Feature  Importance
166                      Do you have an active cancer?    0.162417
188  Are you currently being treated or have you re...    0.123145
124         Do you have painful mouth ulcers or sores?    0.067082
193  Are you more irritable or has your mood been v...    0.056563
167  Have you been unable to move or get up for mor...    0.048299
134  Have you been unintentionally losing weight or...    0.045875
75            Do you have a known severe food allergy?    0.032464
28                     Have you had chills or shivers?    0.030045
123  Are you consulting because you have high blood...    0.020431
26   Have you had sexual intercourse with an HIV-po...    0.020166
76   Have you been in contact with or ate something...    0.018535
106                 Did your cheeks suddenly turn red?    0.018010
16   Have you ever had a sexually transmitted infec...    0.015092
186  Do you have famil

In [37]:
# save feature_importance to csv file
feature_importance.to_csv('/content/drive/MyDrive/DS5500/feature_importance_cv.csv')

In [39]:
top_100_important_features = feature_importance['Feature'].to_list()[:100]
top_100_important_features

['Do you have an active cancer?',
 'Are you currently being treated or have you recently been treated with an oral antibiotic for an ear infection?',
 'Do you have painful mouth ulcers or sores?',
 'Are you more irritable or has your mood been very unstable recently?',
 'Have you been unable to move or get up for more than 3 consecutive days within the last 4 weeks?',
 'Have you been unintentionally losing weight or have you lost your appetite?',
 'Do you have a known severe food allergy?',
 'Have you had chills or shivers?',
 'Are you consulting because you have high blood pressure?',
 'Have you had sexual intercourse with an HIV-positive partner in the past 12 months?',
 'Have you been in contact with or ate something that you have an allergy to?',
 'Did your cheeks suddenly turn red?',
 'Have you ever had a sexually transmitted infection?',
 'Do you have family members who have had lung cancer?',
 'Are you taking any new oral anticoagulants ((NOACs)?',
 'Do you have a known kidney p

In [53]:
correlated_features_to_remove = set(top_100_important_features) - correlated_features
len(correlated_features_to_remove)

27

In [54]:
selected_features = set(top_100_important_features) - correlated_features_to_remove
len(selected_features)

73

In [48]:
top_100_important_features

['Do you have an active cancer?',
 'Are you currently being treated or have you recently been treated with an oral antibiotic for an ear infection?',
 'Do you have painful mouth ulcers or sores?',
 'Are you more irritable or has your mood been very unstable recently?',
 'Have you been unable to move or get up for more than 3 consecutive days within the last 4 weeks?',
 'Have you been unintentionally losing weight or have you lost your appetite?',
 'Do you have a known severe food allergy?',
 'Have you had chills or shivers?',
 'Are you consulting because you have high blood pressure?',
 'Have you had sexual intercourse with an HIV-positive partner in the past 12 months?',
 'Have you been in contact with or ate something that you have an allergy to?',
 'Did your cheeks suddenly turn red?',
 'Have you ever had a sexually transmitted infection?',
 'Do you have family members who have had lung cancer?',
 'Are you taking any new oral anticoagulants ((NOACs)?',
 'Do you have a known kidney p

In [55]:
X_train_selected_no_correlated = X_train[selected_features]
X_test_selected_no_correlated = X_test[selected_features]

In [56]:
clf = XGBClassifier(random_state=23, class_weight='balanced')
clf.fit(X_train_selected_no_correlated, y_train)
# Make predictions
y_pred = clf.predict(X_test_selected_no_correlated)
lb = LabelBinarizer()
y_test_2d = lb.fit_transform(y_test)
y_pred_2d = lb.fit_transform(y_pred)

# Compute scores
accuracy = accuracy_score(y_test, y_pred)
auc_score_ovo = roc_auc_score(y_test_2d, y_pred_2d, multi_class='ovo')
auc_score_ovr = roc_auc_score(y_test_2d, y_pred_2d, multi_class='ovr')
report = classification_report(y_test, y_pred)

# Print scores
print(f'The accuracy score is {accuracy * 100:.2f}%')
print(f'One-vs-One AUC score: {auc_score_ovo * 100:.2f}%')
print(f'One-vs-Rest AUC score: {auc_score_ovr * 100:.2f}%')
print("Classification Report")
print(report)

The accuracy score is 70.41%
One-vs-One AUC score: 51.43%
One-vs-Rest AUC score: 51.43%
Classification Report
              precision    recall  f1-score   support

           0       1.00      0.98      0.99      2153
           1       1.00      0.99      0.99      3302
           2       0.00      0.00      0.00      3214
           3       0.00      0.00      0.00      3509
           4       1.00      0.98      0.99      2598
           5       0.00      0.00      0.00      1829
           6       1.00      0.99      1.00      2411
           7       1.00      1.00      1.00      3798
           8       1.00      0.99      0.99      6770
           9       1.00      0.97      0.99      2831
          10       0.00      0.00      0.00      2083
          11       1.00      0.98      0.99      2454
          12       0.00      0.00      0.00        36
          13       0.11      1.00      0.20      3577
          14       1.00      0.99      0.99      2222
          15       0.96  

# Feature Importance Only

In [57]:
def get_important_features_list_threshold(threshold):
  important_features = []
  for i in range(len(importances)):
    if importances[i] > threshold:
      important_features.append(feature_names[i])
  return important_features

In [36]:
total = 0
for i in range(len(feature_importance)):
    total += importances[i]
print(total)

0.9999999964536497


In [61]:
importances = feature_importance['Importance'].to_list()
features_names = feature_importance['Feature'].to_list()

In [64]:
def get_important_features_list_top(importances, feature_names, threshold):
    importances = np.array(importances)
    # Normalize importances
    importances_normalized = importances / importances.sum()

    # Combine features and their importances
    feature_importances = [(feature, importance) for feature, importance in zip(feature_names, importances_normalized)]

    # Sort the features by their importance
    feature_importances.sort(key=lambda x: x[1], reverse=True)

    # Accumulate the top features until the sum of importances reaches given threshold
    important_features = []
    cumulative_importance = 0.0
    for feature, importance in feature_importances:
        important_features.append(feature)
        cumulative_importance += importance
        if cumulative_importance >= threshold:
            break

    return important_features


## Top Features that Contribute 80%

In [65]:
top_80_percent_important_features = get_important_features_list_top(importances, feature_names, 0.8)

In [66]:
len(top_80_percent_important_features)

27

In [67]:
top_80_X_train = X_train[top_80_percent_important_features]
top_80_X_test = X_test[top_80_percent_important_features]

In [68]:
clf = XGBClassifier(random_state=23, class_weight='balanced')
clf.fit(top_80_X_train, y_train)
# Make predictions
y_pred = clf.predict(top_80_X_test)
lb = LabelBinarizer()
y_test_2d = lb.fit_transform(y_test)
y_pred_2d = lb.fit_transform(y_pred)

# Compute scores
accuracy = accuracy_score(y_test, y_pred)
auc_score_ovo = roc_auc_score(y_test_2d, y_pred_2d, multi_class='ovo')
auc_score_ovr = roc_auc_score(y_test_2d, y_pred_2d, multi_class='ovr')
report = classification_report(y_test, y_pred)

# Print scores
print(f'The accuracy score is {accuracy * 100:.2f}%')
print(f'One-vs-One AUC score: {auc_score_ovo * 100:.2f}%')
print(f'One-vs-Rest AUC score: {auc_score_ovr * 100:.2f}%')
print("Classification Report")
print(report)

The accuracy score is 87.04%
One-vs-One AUC score: 90.83%
One-vs-Rest AUC score: 90.83%
Classification Report
              precision    recall  f1-score   support

           0       1.00      0.76      0.87      2153
           1       0.26      0.93      0.40      3302
           2       0.95      0.42      0.59      3214
           3       1.00      1.00      1.00      3509
           4       0.98      0.99      0.98      2598
           5       0.91      0.41      0.56      1829
           6       0.51      0.63      0.57      2411
           7       1.00      1.00      1.00      3798
           8       0.95      0.99      0.97      6770
           9       0.20      0.01      0.02      2831
          10       1.00      1.00      1.00      2083
          11       0.88      0.85      0.86      2454
          12       1.00      0.67      0.80        36
          13       1.00      0.99      1.00      3577
          14       0.91      0.56      0.69      2222
          15       1.00  

In [69]:
top_90_percent_important_features = get_important_features_list_top(importances, feature_names, 0.9)
len(top_90_percent_important_features)

44

In [70]:
top_90_X_train = X_train[top_90_percent_important_features]
top_90_X_test = X_test[top_90_percent_important_features]

In [71]:
# using top 90%
clf = XGBClassifier(random_state=23, class_weight='balanced')
clf.fit(top_90_X_train, y_train)
# Make predictions
y_pred = clf.predict(top_90_X_test)
lb = LabelBinarizer()
y_test_2d = lb.fit_transform(y_test)
y_pred_2d = lb.fit_transform(y_pred)

# Compute scores
accuracy = accuracy_score(y_test, y_pred)
auc_score_ovo = roc_auc_score(y_test_2d, y_pred_2d, multi_class='ovo')
auc_score_ovr = roc_auc_score(y_test_2d, y_pred_2d, multi_class='ovr')
report = classification_report(y_test, y_pred)

# Print scores
print(f'The accuracy score is {accuracy * 100:.2f}%')
print(f'One-vs-One AUC score: {auc_score_ovo * 100:.2f}%')
print(f'One-vs-Rest AUC score: {auc_score_ovr * 100:.2f}%')
print("Classification Report")
print(report)

The accuracy score is 91.00%
One-vs-One AUC score: 94.21%
One-vs-Rest AUC score: 94.21%
Classification Report
              precision    recall  f1-score   support

           0       1.00      0.97      0.98      2153
           1       0.30      0.91      0.45      3302
           2       0.98      0.83      0.90      3214
           3       1.00      1.00      1.00      3509
           4       1.00      1.00      1.00      2598
           5       0.82      0.51      0.63      1829
           6       0.94      0.98      0.96      2411
           7       1.00      1.00      1.00      3798
           8       0.97      0.99      0.98      6770
           9       0.23      0.02      0.03      2831
          10       1.00      1.00      1.00      2083
          11       0.98      0.98      0.98      2454
          12       1.00      0.78      0.88        36
          13       1.00      1.00      1.00      3577
          14       0.98      0.91      0.94      2222
          15       1.00  

In [ ]:
top_95_percent_important_features = get_important_features_list_top(importances, feature_names, 0.95)
len(top_95_percent_important_features)

58

In [ ]:
top_95_X_train = X_train[top_95_percent_important_features]
top_95_X_test = X_test[top_95_percent_important_features]

In [ ]:
# using top 95%
clf = XGBClassifier(random_state=230, class_weight='balanced')
clf.fit(top_95_X_train, y_train)
# Make predictions
y_pred = clf.predict(top_95_X_test)
lb = LabelBinarizer()
y_test_2d = lb.fit_transform(y_test)
y_pred_2d = lb.fit_transform(y_pred)

# Compute scores
accuracy = accuracy_score(y_test, y_pred)
auc_score_ovo = roc_auc_score(y_test_2d, y_pred_2d, multi_class='ovo')
auc_score_ovr = roc_auc_score(y_test_2d, y_pred_2d, multi_class='ovr')
report = classification_report(y_test, y_pred)

# Print scores
print(f'The accuracy score is {accuracy * 100:.2f}%')
print(f'One-vs-One AUC score: {auc_score_ovo * 100:.2f}%')
print(f'One-vs-Rest AUC score: {auc_score_ovr * 100:.2f}%')
print("Classification Report")
print(report)

The accuracy score is 66.74%
One-vs-One AUC score: 51.36%
One-vs-Rest AUC score: 51.36%
Classification Report
              precision    recall  f1-score   support

           0       1.00      0.89      0.94      2153
           1       1.00      0.91      0.95      3302
           2       0.00      0.00      0.00      3214
           3       1.00      0.80      0.89      3509
           4       0.00      0.00      0.00      2598
           5       0.00      0.00      0.00      1829
           6       1.00      0.99      1.00      2411
           7       1.00      0.96      0.98      3798
           8       1.00      0.96      0.98      6770
           9       1.00      0.97      0.99      2831
          10       1.00      0.81      0.89      2083
          11       1.00      0.94      0.97      2454
          12       0.00      0.00      0.00        36
          13       0.00      0.00      0.00      3577
          14       1.00      0.94      0.97      2222
          15       0.93  

In [ ]:
top_98_percent_important_features = get_important_features_list_top(importances, feature_names, 0.98)
len(top_98_percent_important_features)

77

In [ ]:
top_98_X_train = X_train[top_98_percent_important_features]
top_98_X_test = X_test[top_98_percent_important_features]

In [ ]:
# using top 98%
clf = XGBClassifier(random_state=231, class_weight='balanced')
clf.fit(top_98_X_train, y_train)
# Make predictions
y_pred = clf.predict(top_98_X_test)
lb = LabelBinarizer()
y_test_2d = lb.fit_transform(y_test)
y_pred_2d = lb.fit_transform(y_pred)

# Compute scores
accuracy = accuracy_score(y_test, y_pred)
auc_score_ovo = roc_auc_score(y_test_2d, y_pred_2d, multi_class='ovo')
auc_score_ovr = roc_auc_score(y_test_2d, y_pred_2d, multi_class='ovr')
report = classification_report(y_test, y_pred)

# Print scores
print(f'The accuracy score is {accuracy * 100:.2f}%')
print(f'One-vs-One AUC score: {auc_score_ovo * 100:.2f}%')
print(f'One-vs-Rest AUC score: {auc_score_ovr * 100:.2f}%')
print("Classification Report")
print(report)

The accuracy score is 84.36%
One-vs-One AUC score: 54.11%
One-vs-Rest AUC score: 54.11%
Classification Report
              precision    recall  f1-score   support

           0       1.00      0.96      0.98      2153
           1       1.00      0.97      0.98      3302
           2       0.93      0.86      0.89      3214
           3       1.00      0.80      0.89      3509
           4       1.00      0.83      0.91      2598
           5       0.00      0.00      0.00      1829
           6       1.00      0.99      1.00      2411
           7       1.00      0.96      0.98      3798
           8       1.00      0.99      0.99      6770
           9       1.00      0.97      0.99      2831
          10       1.00      0.81      0.89      2083
          11       1.00      0.94      0.97      2454
          12       0.00      0.00      0.00        36
          13       0.99      0.58      0.73      3577
          14       1.00      0.94      0.97      2222
          15       1.00  

In [ ]:
top_99_percent_important_features = get_important_features_list_top(importances, feature_names, 0.99)
len(top_99_percent_important_features)

90

In [ ]:
top_99_X_train = X_train[top_99_percent_important_features]
top_99_X_test = X_test[top_99_percent_important_features]

In [ ]:
# using top 99%
clf = XGBClassifier(random_state=232, class_weight='balanced')
clf.fit(top_99_X_train, y_train)
# Make predictions
y_pred = clf.predict(top_99_X_test)
lb = LabelBinarizer()
y_test_2d = lb.fit_transform(y_test)
y_pred_2d = lb.fit_transform(y_pred)

# Compute scores
accuracy = accuracy_score(y_test, y_pred)
auc_score_ovo = roc_auc_score(y_test_2d, y_pred_2d, multi_class='ovo')
auc_score_ovr = roc_auc_score(y_test_2d, y_pred_2d, multi_class='ovr')
report = classification_report(y_test, y_pred)

# Print scores
print(f'The accuracy score is {accuracy * 100:.2f}%')
print(f'One-vs-One AUC score: {auc_score_ovo * 100:.2f}%')
print(f'One-vs-Rest AUC score: {auc_score_ovr * 100:.2f}%')
print("Classification Report")
print(report)

The accuracy score is 86.97%
One-vs-One AUC score: 54.07%
One-vs-Rest AUC score: 54.07%
Classification Report
              precision    recall  f1-score   support

           0       1.00      0.96      0.98      2153
           1       1.00      0.97      0.98      3302
           2       0.93      0.86      0.89      3214
           3       1.00      0.80      0.89      3509
           4       1.00      0.83      0.91      2598
           5       0.00      0.00      0.00      1829
           6       1.00      0.99      1.00      2411
           7       0.98      1.00      0.99      3798
           8       1.00      1.00      1.00      6770
           9       1.00      0.97      0.99      2831
          10       1.00      0.81      0.89      2083
          11       1.00      0.94      0.97      2454
          12       0.00      0.00      0.00        36
          13       1.00      0.58      0.73      3577
          14       1.00      0.94      0.97      2222
          15       1.00  

In [ ]:
# Perform Cross Validation  - Took 20 Minutes

from sklearn.model_selection import cross_validate

# Initialize the model
clf = XGBClassifier(random_state=0, class_weight='balanced')

# Perform cross validation
cv_results = cross_validate(clf, top_99_X_train, y_train, cv=5, scoring=['accuracy', 'precision_macro', 'recall_macro', 'f1_macro', 'roc_auc_ovr', 'roc_auc_ovo'], return_estimator=True)

# Print the mean scores
print(f'Mean Accuracy: {cv_results["test_accuracy"].mean() * 100:.2f}%')
print(f'Mean ROC_AUC OVR: {cv_results["test_roc_auc_ovr"].mean() * 100:.2f}%')
print(f'Mean ROC_AUC OVO: {cv_results["test_roc_auc_ovo"].mean() * 100:.2f}%')
print(f'Mean Precision: {cv_results["test_precision_macro"].mean() * 100:.2f}%')
print(f'Mean Recall: {cv_results["test_recall_macro"].mean() * 100:.2f}%')
print(f'Mean F1 Score: {cv_results["test_f1_macro"].mean() * 100:.2f}%')

Mean Accuracy: 86.71%
Mean ROC_AUC OVR: 98.88%
Mean ROC_AUC OVO: 98.57%
Mean Precision: 88.74%
Mean Recall: 83.19%
Mean F1 Score: 84.80%


In [ ]:
top_995_percent_important_features = get_important_features_list_top(importances, feature_names, 0.995)
len(top_995_percent_important_features)

102

In [ ]:
pprint(top_995_percent_important_features)

['Have you had sexual intercourse with an HIV-positive partner in the past 12 '
 'months?',
 'Do you have an active cancer?',
 'Are you more irritable or has your mood been very unstable recently?',
 'Do you have painful mouth ulcers or sores?',
 'Are you currently being treated or have you recently been treated with an '
 'oral antibiotic for an ear infection?',
 'Have you been unable to move or get up for more than 3 consecutive days '
 'within the last 4 weeks?',
 'Do you have a known kidney problem resulting in an inability to retain '
 'proteins?',
 'Have you been in contact with or ate something that you have an allergy to?',
 'Have you had chills or shivers?',
 'Do you have a known severe food allergy?',
 'Are you consulting because you have high blood pressure?',
 'Did your cheeks suddenly turn red?',
 'Have you been unintentionally losing weight or have you lost your appetite?',
 'Are you taking any new oral anticoagulants ((NOACs)?',
 'Have you had unprotected sex with more t

In [ ]:
top_995_X_train = X_train[top_995_percent_important_features]
top_995_X_test = X_test[top_995_percent_important_features]

In [ ]:
# using top 99.5%
clf = XGBClassifier(random_state=232, class_weight='balanced')
clf.fit(top_995_X_train, y_train)
# Make predictions
y_pred = clf.predict(top_995_X_test)
lb = LabelBinarizer()
y_test_2d = lb.fit_transform(y_test)
y_pred_2d = lb.fit_transform(y_pred)

# Compute scores
accuracy = accuracy_score(y_test, y_pred)
auc_score_ovo = roc_auc_score(y_test_2d, y_pred_2d, multi_class='ovo')
auc_score_ovr = roc_auc_score(y_test_2d, y_pred_2d, multi_class='ovr')
report = classification_report(y_test, y_pred)

# Print scores
print(f'The accuracy score is {accuracy * 100:.2f}%')
print(f'One-vs-One AUC score: {auc_score_ovo * 100:.2f}%')
print(f'One-vs-Rest AUC score: {auc_score_ovr * 100:.2f}%')
print("Classification Report")
print(report)

The accuracy score is 93.25%
One-vs-One AUC score: 96.33%
One-vs-Rest AUC score: 96.33%
Classification Report
              precision    recall  f1-score   support

           0       1.00      0.98      0.99      2153
           1       1.00      0.97      0.98      3302
           2       0.97      0.86      0.91      3214
           3       0.88      0.90      0.89      3509
           4       1.00      1.00      1.00      2598
           5       1.00      0.45      0.63      1829
           6       1.00      0.99      1.00      2411
           7       1.00      1.00      1.00      3798
           8       1.00      1.00      1.00      6770
           9       1.00      0.97      0.99      2831
          10       1.00      0.81      0.89      2083
          11       1.00      1.00      1.00      2454
          12       1.00      0.61      0.76        36
          13       1.00      0.66      0.80      3577
          14       1.00      0.99      0.99      2222
          15       0.96  

In [ ]:
# Perform Cross Validation  - Took 20 minutes

from sklearn.model_selection import cross_validate

# Initialize the model
clf = XGBClassifier(random_state=0, class_weight='balanced')

# Perform cross validation
cv_results = cross_validate(clf, top_995_X_train, y_train, cv=5, scoring=['accuracy', 'precision_macro', 'recall_macro', 'f1_macro', 'roc_auc_ovr', 'roc_auc_ovo'], return_estimator=True)

# Print the mean scores
print(f'Mean Accuracy: {cv_results["test_accuracy"].mean() * 100:.2f}%')
print(f'Mean ROC_AUC OVR: {cv_results["test_roc_auc_ovr"].mean() * 100:.2f}%')
print(f'Mean ROC_AUC OVO: {cv_results["test_roc_auc_ovo"].mean() * 100:.2f}%')
print(f'Mean Precision: {cv_results["test_precision_macro"].mean() * 100:.2f}%')
print(f'Mean Recall: {cv_results["test_recall_macro"].mean() * 100:.2f}%')
print(f'Mean F1 Score: {cv_results["test_f1_macro"].mean() * 100:.2f}%')

Mean Accuracy: 93.42%
Mean ROC_AUC OVR: 99.81%
Mean ROC_AUC OVO: 99.80%
Mean Precision: 96.17%
Mean Recall: 92.74%
Mean F1 Score: 93.37%


In [ ]:
# Generate feature importances

for idx, model in enumerate(cv_results['estimator']):
    # Extract feature importances
    importances = model.feature_importances_

    # Get the feature names
    print(f'Model {idx}')
    feature_names = X_train.columns

    # Create a DataFrame for the importances
    feature_importance = pd.DataFrame({
        'Feature': feature_names,
        'Importance': importances
    })

# Sort the DataFrame by the importances
feature_importance = feature_importance.sort_values(by='Importance', ascending=False)

# Display the top features
print(feature_importance.head(50))

In [ ]:
# Generate feature importances

for idx, model in enumerate(cv_results['estimator']):
    # Extract feature importances
    importances = model.feature_importances_

    # Get the feature names
    print(f'Model {idx}')
    feature_names = X_train.columns

    # Create a DataFrame for the importances
    feature_importance = pd.DataFrame({
        'Feature': feature_names,
        'Importance': importances
    })

# Sort the DataFrame by the importances
feature_importance = feature_importance.sort_values(by='Importance', ascending=False)

# Display the top features
print(feature_importance.head(50))



Model 0
Model 1
Model 2
Model 3
Model 4
                                               Feature  Importance
166                      Do you have an active cancer?    0.162417
188  Are you currently being treated or have you re...    0.123145
124         Do you have painful mouth ulcers or sores?    0.067082
193  Are you more irritable or has your mood been v...    0.056563
167  Have you been unable to move or get up for mor...    0.048299
134  Have you been unintentionally losing weight or...    0.045875
75            Do you have a known severe food allergy?    0.032464
28                     Have you had chills or shivers?    0.030045
123  Are you consulting because you have high blood...    0.020431
26   Have you had sexual intercourse with an HIV-po...    0.020166
76   Have you been in contact with or ate something...    0.018535
106                 Did your cheeks suddenly turn red?    0.018010
16   Have you ever had a sexually transmitted infec...    0.015092
186  Do you have famil

In [ ]:
feature_importance.describe

<bound method NDFrame.describe of                                                Feature  Importance
166                      Do you have an active cancer?    0.162417
188  Are you currently being treated or have you re...    0.123145
124         Do you have painful mouth ulcers or sores?    0.067082
193  Are you more irritable or has your mood been v...    0.056563
167  Have you been unable to move or get up for mor...    0.048299
..                                                 ...         ...
147  Were you diagnosed with endocrine disease or a...    0.000000
206  Have you breastfed one of your children for mo...    0.000000
118                  Do you have chronic pancreatitis?    0.000000
120            Do you have pale stools and dark urine?    0.000000
172  Have you been in contact with someone who has ...    0.000000

[216 rows x 2 columns]>

# Recursive Feacture Elimintation

In [ ]:
from sklearn.feature_selection import RFE

def select_most_important_features(num_features, X_train, y_train):
    estimator = XGBClassifier()
    selector = RFE(estimator, n_features_to_select=num_features, step=1)
    selector = selector.fit(X_train, y_train)
    selected_features = X_train.columns[selector.support_]
    feature_ranking = selector.ranking_
    return selected_features, feature_ranking, selector

In [ ]:
top_50_features, feature_ranking, selector = select_most_important_features(50, top_995_X_train, y_train) # took 3hrs 27 minutes
print(top_50_features)

Index(['Have you had sexual intercourse with an HIV-positive partner in the past 12 months?',
       'Do you have an active cancer?',
       'Are you more irritable or has your mood been very unstable recently?',
       'Do you have painful mouth ulcers or sores?',
       'Are you currently being treated or have you recently been treated with an oral antibiotic for an ear infection?',
       'Have you been unable to move or get up for more than 3 consecutive days within the last 4 weeks?',
       'Do you have a known kidney problem resulting in an inability to retain proteins?',
       'Do you have a known severe food allergy?',
       'Are you consulting because you have high blood pressure?',
       'Did your cheeks suddenly turn red?',
       'Have you been unintentionally losing weight or have you lost your appetite?',
       'Are you taking any new oral anticoagulants ((NOACs)?',
       'Have you had unprotected sex with more than one partner in the last 6 months?',
       'Have y

In [ ]:
X_train_selected = selector.transform(top_995_X_train)
X_test_selected = selector.transform(top_995_X_test)

In [ ]:
# Perform Cross Validation  - Took 14 minutes

from sklearn.model_selection import cross_validate

# Initialize the model
clf = XGBClassifier(random_state=0, class_weight='balanced')

# Perform cross validation
cv_results = cross_validate(clf, X_train_selected, y_train, cv=5, scoring=['accuracy', 'precision_macro', 'recall_macro', 'f1_macro', 'roc_auc_ovr', 'roc_auc_ovo'], return_estimator=True)

# Print the mean scores
print(f'Mean Accuracy: {cv_results["test_accuracy"].mean() * 100:.2f}%')
print(f'Mean ROC_AUC OVR: {cv_results["test_roc_auc_ovr"].mean() * 100:.2f}%')
print(f'Mean ROC_AUC OVO: {cv_results["test_roc_auc_ovo"].mean() * 100:.2f}%')
print(f'Mean Precision: {cv_results["test_precision_macro"].mean() * 100:.2f}%')
print(f'Mean Recall: {cv_results["test_recall_macro"].mean() * 100:.2f}%')
print(f'Mean F1 Score: {cv_results["test_f1_macro"].mean() * 100:.2f}%')

Mean Accuracy: 62.30%
Mean ROC_AUC OVR: 90.91%
Mean ROC_AUC OVO: 91.37%
Mean Precision: 69.06%
Mean Recall: 60.12%
Mean F1 Score: 63.17%


# Feature Selection for Top 10 Diseases by Frequency Distribution

In [146]:
# Top 10 diseases
list(train_df['PATHOLOGY'].value_counts().index[:10])

['URTI',
 'Viral pharyngitis',
 'Anemia',
 'HIV (initial infection)',
 'Localized edema',
 'Anaphylaxis',
 'Pulmonary embolism',
 'Influenza',
 'Bronchitis',
 'Allergic sinusitis']

In [144]:
# Get pathology distribution sorted
pathology_distribution = train_encoded['PATHOLOGY'].value_counts()
top_10_pathologies = pathology_distribution.index[:10]
list(top_10_pathologies)

[44, 46, 8, 23, 27, 7, 36, 13, 6, 1]

In [88]:
top_10_pathologies_train_df = train_encoded[train_encoded['PATHOLOGY'].isin(top_10_pathologies)]
len(top_10_pathologies_train_df)

366303

In [89]:
top_10_pathologies_test_df = test_encoded[test_encoded['PATHOLOGY'].isin(top_10_pathologies)]
len(top_10_pathologies_test_df)

48222

In [90]:
# Prepare training and test variables
X_columns = [col for col in top_10_pathologies_train_df.columns if col not in ['Unnamed: 0', 'PATHOLOGY']]
X_train = top_10_pathologies_train_df[X_columns]
y_train = top_10_pathologies_train_df['PATHOLOGY']
X_test = top_10_pathologies_test_df[X_columns]
y_test = top_10_pathologies_test_df['PATHOLOGY']
pprint(f'X_train shape: {X_train.shape}')
pprint(f'y_train shape: {y_train.shape}')
pprint(f'X_test shape: {X_test.shape}')
pprint(f'y_test shape: {y_test.shape}')

'X_train shape: (366303, 216)'
'y_train shape: (366303,)'
'X_test shape: (48222, 216)'
'y_test shape: (48222,)'


In [95]:
y_train.unique()

array([44, 23, 46,  8,  6,  7, 13, 27, 36,  1])

In [97]:
# XGBoost expects classess to start from 0, so create a new mapping to fit this.
unique_classes = np.unique(y_train)
class_mapping = {original: new for new, original in enumerate(unique_classes)}

y_train_mapped = y_train.map(class_mapping)
y_test_mapped = y_test.map(class_mapping)

In [98]:
y_train_mapped.unique()

array([8, 5, 9, 3, 1, 2, 4, 6, 7, 0])

In [106]:
important_features_by_pathologies = {}
roc_auc_scores = {}
accuracy_scores = {}


for pathology in list(top_10_pathologies):

    # Initialize and train the model
    model = XGBClassifier(class_weight='balanced', alpha=1.0)
    model.fit(X_train, y_train_mapped)

     # Predict and evaluate
    predictions = model.predict(X_test)
    roc_auc_ovr = roc_auc_score(y_test_mapped, model.predict_proba(X_test), multi_class='ovr')
    accuracy = accuracy_score(y_test_mapped, predictions)
    roc_auc_scores[pathology] = roc_auc_ovr.tolist()
    accuracy_scores[pathology] = accuracy

    # Get feature importances
    importances = model.feature_importances_
    feature_names = X_train.columns
    features_importance = zip(feature_names, importances)

    # Sort features by importance
    sorted_features = sorted(features_importance, key=lambda x: x[1], reverse=True)

    # Store the top features for this disease
    important_features_by_pathologies[pathology] = sorted_features


In [129]:
len(important_features_by_pathologies)

10

In [147]:
from collections import Counter

# Count how often each feature is important across diseases
feature_counts = Counter()

for pathology in important_features_by_pathologies:
    for feature, importance in important_features_by_pathologies[pathology]:
        if importance > 0.005:  # You can set a threshold for importance
            feature_counts[feature] += 1

# Sort features by their count
sorted_feature_counts = sorted(feature_counts.items(), key=lambda x: x[1], reverse=True)


In [148]:
len(sorted_feature_counts)

20

In [149]:
# Get list of features
selected_features = [feature for feature, count in sorted_feature_counts]
pprint(selected_features)

['Do you have swollen or painful lymph nodes?',
 'Have you had sexual intercourse with an HIV-positive partner in the past 12 '
 'months?',
 'Are you taking any new oral anticoagulants ((NOACs)?',
 'Have you had unprotected sex with more than one partner in the last 6 '
 'months?',
 'Is your nose or the back of your throat itchy?',
 'Are you immunosuppressed?',
 'Have you had surgery within the last month?',
 'Do you have a chronic obstructive pulmonary disease (COPD)?',
 'Do you regularly take stimulant drugs?',
 'Are you exposed to secondhand cigarette smoke on a daily basis?',
 'Do you have heart failure?',
 'What color is the rash?',
 'Have you ever had a diagnosis of anemia?',
 'Where is the swelling located?',
 'Have you ever had a sexually transmitted infection?',
 'Where is the affected region located?',
 'Do you have any lesions, redness or problems on your skin that you believe '
 'are related to the condition you are consulting for?',
 'Have you started or taken any antipsyc

In [150]:
X_train_selected = X_train[selected_features]
X_test_selected = X_test[selected_features]

In [151]:
X_train_selected

Do you have swollen or painful lymph nodes?  \
0                                               0.0   
1                                               1.0   
3                                               0.0   
4                                               0.0   
6                                               0.0   
...                                             ...   
980259                                          0.0   
980260                                          0.0   
980261                                          1.0   
980262                                          0.0   
980263                                          0.0   

        Have you had sexual intercourse with an HIV-positive partner in the past 12 months?  \
0                                                     0.0                                     
1                                                     1.0                                     
3                                                     0.0                                     
4                                                     0.0                                     
6                                                     0.0                                     
...                                                   ...                                     
980259                                                0.0                                     
980260                                                0.0                                     
980261                                                1.0                                     
980262                                                1.0                                     
980263                                                0.0                                     

        Are you taking any new oral anticoagulants ((NOACs)?  \
0                                                     0.0      
1                                                     0.0      
3                                                     0.0      
4                                                     0.0      
6                                                     0.0      
...                                                   ...      
980259                                                0.0      
980260                                                0.0      
980261                                                0.0      
980262                                                0.0      
980263                                                0.0      

        Have you had unprotected sex with more than one partner in the last 6 months?  \
0                                                     0.0                               
1                                                     1.0                               
3                                                     0.0                               
4                                                     0.0                               
6                                                     0.0                               
...                                                   ...                               
980259                                                1.0                               
980260                                                1.0                               
980261                                                1.0                               
980262                                                1.0                               
980263                                                1.0                               

        Is your nose or the back of your throat itchy?  \
0                                                  0.0   
1                                                  0.0   
3                                                  0.0   
4                                                  0.0   
6                                                  0.0   
...                 

In [152]:
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, roc_auc_score
# Initialize the model
clf = XGBClassifier(random_state=0, class_weight='balanced')

# Perform cross-validation
cv_results = cross_validate(clf, X_train_selected, y_train_mapped, cv=5,
                            scoring=['accuracy', 'precision_macro', 'recall_macro', 'f1_macro', 'roc_auc_ovr', 'roc_auc_ovo'],
                            return_estimator=True)

# Prepare to store test scores
test_scores = {
    'accuracy': [],
    'precision_macro': [],
    'recall_macro': [],
    'f1_macro': [],
    'roc_auc_ovr': [],
    'roc_auc_ovo': []
}

# Predict on X_test with each fold's estimator
for estimator in cv_results['estimator']:
    y_pred = estimator.predict(X_test_selected)
    y_pred_proba = estimator.predict_proba(X_test_selected)

    test_scores['accuracy'].append(accuracy_score(y_test_mapped, y_pred))
    test_scores['precision_macro'].append(precision_score(y_test_mapped, y_pred, average='macro'))
    test_scores['recall_macro'].append(recall_score(y_test_mapped, y_pred, average='macro'))
    test_scores['f1_macro'].append(f1_score(y_test_mapped, y_pred, average='macro'))
    test_scores['roc_auc_ovr'].append(roc_auc_score(y_test_mapped, y_pred_proba, multi_class='ovr'))
    test_scores['roc_auc_ovo'].append(roc_auc_score(y_test_mapped, y_pred_proba, multi_class='ovo'))

# Calculate and print mean test scores
for metric, scores in test_scores.items():
    print(f'Mean {metric}: {np.mean(scores) * 100:.2f}%')

Mean accuracy: 90.90%
Mean precision_macro: 96.30%
Mean recall_macro: 93.35%
Mean f1_macro: 93.92%
Mean roc_auc_ovr: 99.38%
Mean roc_auc_ovo: 99.61%


In [153]:
clf = XGBClassifier(random_state=27, class_weight='balanced')
clf.fit(X_train_selected, y_train_mapped)
# Make predictions
y_pred = clf.predict(X_test_selected)
lb = LabelBinarizer()
y_test_2d = lb.fit_transform(y_test_mapped)
y_pred_2d = lb.fit_transform(y_pred)

# Compute scores
accuracy = accuracy_score(y_test_mapped, y_pred)
auc_score_ovo = roc_auc_score(y_test_2d, y_pred_2d, multi_class='ovo')
auc_score_ovr = roc_auc_score(y_test_2d, y_pred_2d, multi_class='ovr')
report = classification_report(y_test_mapped, y_pred)

# Print scores
print(f'The accuracy score is {accuracy * 100:.2f}%')
print(f'One-vs-One AUC score: {auc_score_ovo * 100:.2f}%')
print(f'One-vs-Rest AUC score: {auc_score_ovr * 100:.2f}%')
print("Classification Report")
print(report)

The accuracy score is 90.90%
One-vs-One AUC score: 96.13%
One-vs-Rest AUC score: 96.13%
Classification Report
              precision    recall  f1-score   support

           0       0.97      1.00      0.99      3302
           1       1.00      0.96      0.98      2411
           2       1.00      1.00      1.00      3798
           3       1.00      0.96      0.98      6770
           4       1.00      0.79      0.89      3577
           5       1.00      1.00      1.00      3904
           6       1.00      1.00      1.00      3734
           7       1.00      1.00      1.00      3679
           8       1.00      0.63      0.77      8713
           9       0.66      1.00      0.80      8334

    accuracy                           0.91     48222
   macro avg       0.96      0.93      0.94     48222
weighted avg       0.94      0.91      0.91     48222

